# FSS unit cell simulation

This example shows how to use PyAEDT to model and simulate a unit cell
for a frequency-selective surface in HFSS.

Keywords: **HFSS**, **FSS**, **Floquet**.

## Perform imports and define constants

Perform required imports.

In [1]:
import os
import tempfile
import time

In [2]:
import ansys.aedt.core

Define constants.

In [3]:
AEDT_VERSION = "2024.2"
NG_MODE = False  # Open AEDT UI when it is launched.

## Create temporary directory

Create a temporary directory where downloaded data or
dumped data can be stored.
If you'd like to retrieve the project data for subsequent use,
the temporary folder name is given by ``temp_folder.name``.

In [4]:
temp_folder = tempfile.TemporaryDirectory(suffix=".ansys")

## Launch AEDT

In [5]:
project_name = os.path.join(temp_folder.name, "FSS.aedt")
d = ansys.aedt.core.launch_desktop(
    AEDT_VERSION,
    non_graphical=NG_MODE,
    new_desktop=True,
)

PyAEDT INFO: Python version 3.10.11 (tags/v3.10.11:7d4cc5a, Apr  5 2023, 00:38:17) [MSC v.1929 64 bit (AMD64)]


PyAEDT INFO: PyAEDT version 0.12.dev0.


PyAEDT INFO: Initializing new Desktop session.


PyAEDT INFO: Log on console is enabled.


PyAEDT INFO: Log on file C:\Users\ansys\AppData\Local\Temp\pyaedt_ansys_aca01341-c288-4ef7-b7ac-1247b1ea9f52.log is enabled.


...

PyAEDT INFO: Debug logger is disabled. PyAEDT methods will not be logged.


PyAEDT INFO: Launching PyAEDT with gRPC plugin.


PyAEDT INFO: New AEDT session is starting on gRPC port 56334


PyAEDT INFO: AEDT installation Path C:\Program Files\AnsysEM\v242\Win64


PyAEDT INFO: Ansoft.ElectronicsDesktop.2024.2 version started with process ID 6696.


## Launch HFSS

Create an HFSS design.

In [6]:
hfss = ansys.aedt.core.Hfss(
    version=AEDT_VERSION, project=project_name, solution_type="Modal"
)

PyAEDT INFO: Python version 3.10.11 (tags/v3.10.11:7d4cc5a, Apr  5 2023, 00:38:17) [MSC v.1929 64 bit (AMD64)]


PyAEDT INFO: PyAEDT version 0.12.dev0.


PyAEDT INFO: Returning found Desktop session with PID 6696!


PyAEDT INFO: Project FSS has been created.


PyAEDT INFO: No design is present. Inserting a new design.


PyAEDT INFO: Added design 'HFSS_1Y0' of type HFSS.


PyAEDT INFO: Aedt Objects correctly read


## Define variable

Define a variable for the 3D component.

In [7]:
hfss["patch_dim"] = "10mm"

## Set up model

Download the 3D component from the example data and insert the 3D component.

In [8]:
unitcell_3d_component_path = ansys.aedt.core.downloads.download_FSS_3dcomponent(
    destination=temp_folder.name
)
unitcell_path = os.path.join(unitcell_3d_component_path, "FSS_unitcell_23R2.a3dcomp")
comp = hfss.modeler.insert_3d_component(unitcell_path)

PyAEDT INFO: Modeler class has been initialized! Elapsed time: 0m 1sec


PyAEDT INFO: Parsing C:/Users/ansys/AppData/Local/Temp/tmp5nbqpnnw.ansys/FSS.aedt.


PyAEDT INFO: File C:/Users/ansys/AppData/Local/Temp/tmp5nbqpnnw.ansys/FSS.aedt correctly loaded. Elapsed time: 0m 0sec


PyAEDT INFO: aedt file load time 0.0157315731048584


Assign the parameter to the 3D component.

In [9]:
component_name = hfss.modeler.user_defined_component_names
comp.parameters["a"] = "patch_dim"

Create an open region along +Z direction for unit cell analysis.

In [10]:
bounding_dimensions = hfss.modeler.get_bounding_dimension()

periodicity_x = bounding_dimensions[0]
periodicity_y = bounding_dimensions[1]

region = hfss.modeler.create_air_region(
    z_pos=10 * bounding_dimensions[2],
    is_percentage=False,
)

[x_min, y_min, z_min, x_max, y_max, z_max] = region.bounding_box

Assign the lattice pair boundary condition.

In [11]:
hfss.auto_assign_lattice_pairs(assignment=region.name)

['LatticePair1', 'LatticePair2']

Define the Floquet port.

In [12]:
id_z_pos = region.top_face_z
hfss.create_floquet_port(
    assignment=id_z_pos,
    lattice_origin=[0, 0, z_max],
    lattice_a_end=[0, y_max, z_max],
    lattice_b_end=[x_max, 0, z_max],
    name="port_z_max",
    deembed_distance=10 * bounding_dimensions[2],
)

PyAEDT INFO: Boundary Floquet Port port_z_max has been correctly created.


Create a solution setup, including the frequency sweep.

In [13]:
setup = hfss.create_setup("MySetup")
setup.props["Frequency"] = "10GHz"
setup.props["MaximumPasses"] = 10
hfss.create_linear_count_sweep(
    setup=setup.name,
    units="GHz",
    start_frequency=6,
    stop_frequency=15,
    num_of_freq_points=51,
    name="sweep1",
    sweep_type="Interpolating",
    interpolation_tol=6,
    save_fields=False,
)

PyAEDT INFO: Linear count sweep sweep1 has been correctly created.


## Postprocess

Create S-parameter reports.

In [14]:
all_quantities = hfss.post.available_report_quantities()
str_mag = []
str_ang = []

variation = {"Freq": ["All"]}

for i in all_quantities:
    str_mag.append("mag(" + i + ")")
    str_ang.append("ang_deg(" + i + ")")

hfss.post.create_report(
    expressions=str_mag,
    variations=variation,
    plot_name="magnitude_plot",
)
hfss.post.create_report(
    expressions=str_ang,
    variations=variation,
    plot_name="phase_plot",
)

PyAEDT INFO: PostProcessor class has been initialized! Elapsed time: 0m 0sec


PyAEDT INFO: Post class has been initialized! Elapsed time: 0m 0sec


## Save and run simulation

Save and run the simulation. Uncomment the following line to run the analysis.

In [15]:
# hfss.analyze()
hfss.save_project()

PyAEDT INFO: Project FSS Saved correctly


True

## Release AEDT

In [16]:
hfss.release_desktop()
# Wait 3 seconds to allow AEDT to shut down before cleaning the temporary directory.
time.sleep(3)

PyAEDT INFO: Desktop has been released and closed.


## Clean up

All project files are saved in the folder ``temp_folder.name``.
If you've run this example as a Jupyter notebook, you
can retrieve those project files. The following cell removes
all temporary files, including the project folder.

In [17]:
temp_folder.cleanup()